In [4]:
!poetry install --no-root

Installing dependencies from lock file

Package operations: 17 installs, 6 updates, 0 removals

  - Downgrading attrs (25.1.0 -> 24.3.0): Pending...
  - Downgrading attrs (25.1.0 -> 24.3.0): Installing...
  - Downgrading attrs (25.1.0 -> 24.3.0)
  - Installing ruamel-yaml-clib (0.2.12): Pending...
  - Installing ruamel-yaml-clib (0.2.12): Downloading... 0%
  - Installing ruamel-yaml-clib (0.2.12): Downloading... 80%
  - Installing ruamel-yaml-clib (0.2.12): Downloading... 100%
  - Installing ruamel-yaml-clib (0.2.12): Installing...
  - Installing ruamel-yaml-clib (0.2.12)
  - Installing ruamel-yaml (0.18.10): Pending...
  - Installing svgwrite (1.4.3): Pending...
  - Installing wrapt (1.17.2): Pending...
  - Installing svgwrite (1.4.3): Pending...
  - Installing wrapt (1.17.2): Pending...
  - Installing ruamel-yaml (0.18.10): Downloading... 0%
  - Installing svgwrite (1.4.3): Pending...
  - Installing wrapt (1.17.2): Pending...
  - Installing svgwrite (1.4.3): Pending...
  - Installing

In [6]:
import os
from collections import Counter
import logging
import sys
from pathlib import Path
import subprocess
import os
import matplotlib.pyplot as plt
import seaborn as sns
from IPython.display import display, HTML
import IPython
import pandas as pd
# from tqdm import tqdm
import seaborn as sns
import ast
from tqdm.notebook import tqdm
import networkx as nx

from dotenv import load_dotenv

In [7]:
def find_comp_gen_dir():
    """Find the computational_genetic_genealogy directory by searching up from current directory."""
    current = Path.cwd()
    
    # Search up through parent directories
    while current != current.parent:
        # Check if target directory exists in current path
        target = current / 'computational_genetic_genealogy'
        if target.is_dir():
            return target
        # Move up one directory
        current = current.parent
    
    raise FileNotFoundError("Could not find computational_genetic_genealogy directory")

def load_env_file():
    """Find and load the .env file from the computational_genetic_genealogy directory."""
    try:
        # Find the computational_genetic_genealogy directory
        comp_gen_dir = find_comp_gen_dir()
        
        # Look for .env file
        env_path = comp_gen_dir / '.env'
        if not env_path.exists():
            print(f"Warning: No .env file found in {comp_gen_dir}")
            return None
        
        # Load the .env file
        load_dotenv(env_path, override=True)
        print(f"Loaded environment variables from: {env_path}")
        return env_path
        
    except FileNotFoundError as e:
        print(f"Error: {e}")
        return None

# Use the function
env_path = load_env_file()

working_directory = os.getenv('PROJECT_WORKING_DIR', default=None)
data_directory = os.getenv('PROJECT_DATA_DIR', default=None)
references_directory = os.getenv('PROJECT_REFERENCES_DIR', default=None)
results_directory = os.getenv('PROJECT_RESULTS_DIR', default=None)
utils_directory = os.getenv('PROJECT_UTILS_DIR', default=None)

os.environ["WORKING_DIRECTORY"] = working_directory
os.environ["DATA_DIRECTORY"] = data_directory
os.environ["REFERENCES_DIRECTORY"] = references_directory
os.environ["RESULTS_DIRECTORY"] = results_directory
os.environ["UTILS_DIRECTORY"] = utils_directory

print(f"Working Directory: {working_directory}")
print(f"Data Directory: {data_directory}")
print(f"References Directory: {references_directory}")
print(f"Results Directory: {results_directory}")
print(f"Utils Directory: {utils_directory}")

os.chdir(working_directory)
print(f"The current directory is {os.getcwd()}")

Loaded environment variables from: /home/lakishadavid/computational_genetic_genealogy/.env
Working Directory: /home/lakishadavid/computational_genetic_genealogy
Data Directory: /home/lakishadavid/computational_genetic_genealogy/data
References Directory: /home/lakishadavid/computational_genetic_genealogy/references
Results Directory: /home/lakishadavid/computational_genetic_genealogy/results
Utils Directory: /home/lakishadavid/computational_genetic_genealogy/utils
The current directory is /home/lakishadavid/computational_genetic_genealogy


In [8]:
def configure_logging(log_filename, log_file_debug_level="INFO", console_debug_level="INFO"):
    """
    Configure logging for both file and console handlers.

    Args:
        log_filename (str): Path to the log file where logs will be written.
        log_file_debug_level (str): Logging level for the file handler.
        console_debug_level (str): Logging level for the console handler.
    """
    # Create a root logger
    logger = logging.getLogger()
    logger.setLevel(logging.DEBUG)  # Capture all messages at the root level

    # Convert level names to numeric levels
    file_level = getattr(logging, log_file_debug_level.upper(), logging.INFO)
    console_level = getattr(logging, console_debug_level.upper(), logging.INFO)

    # File handler: Logs messages at file_level and above to the file
    file_handler = logging.FileHandler(log_filename)
    file_handler.setLevel(file_level)
    file_formatter = logging.Formatter('%(asctime)s - %(levelname)s - %(message)s')
    file_handler.setFormatter(file_formatter)

    # Console handler: Logs messages at console_level and above to the console
    console_handler = logging.StreamHandler(sys.stdout)
    console_handler.setLevel(console_level)
    console_formatter = logging.Formatter('%(asctime)s - %(levelname)s - %(message)s')
    console_handler.setFormatter(console_formatter)

    # Add handlers to the root logger
    logger.addHandler(file_handler)
    logger.addHandler(console_handler)
    
def clear_logger():
    """Remove all handlers from the root logger."""
    logger = logging.getLogger()
    for handler in logger.handlers[:]:
        logger.removeHandler(handler)
        
log_filename = os.path.join(results_directory, "labX_log.txt")
print(f"The Lab X log file is located at {log_filename}.")

# Ensure the results_directory exists
if not os.path.exists(results_directory):
    os.makedirs(results_directory)

# Check if the file exists; if not, create it
if not os.path.exists(log_filename):
    with open(log_filename, 'w') as file:
        pass  # The file is now created.
    
clear_logger() # Clear the logger before reconfiguring it
configure_logging(log_filename, log_file_debug_level="INFO", console_debug_level="INFO")

The Lab X log file is located at /home/lakishadavid/computational_genetic_genealogy/results/labX_log.txt.


### Define the demographic model

The stdpopsim package maintains demography models and genetic maps. Check the documentation for the demograhy of your choice. You can also build your own demography model.

In [9]:
import stdpopsim

species = stdpopsim.get_species("HomSap")

# https://www.ncbi.nlm.nih.gov/pmc/articles/PMC4788123/
# mutation_rate = 1.4e-8
# https://www.ncbi.nlm.nih.gov/pmc/articles/PMC1461236/
# mutation_rate = 2.5e-8
# The value used by stdpopsim
mutation_rate = 1.29e-08

# Demographic model for American admixture, taken from Browning et al. 2011
# https://popsim-consortium.github.io/stdpopsim-docs/stable/catalog.html#sec_catalog_homsap_models_americanadmixture_4b11
# populations: ADMIX, AFR, ASIA, EUR
# to build this model, see https://tskit.dev/msprime/docs/stable/demography.html#sec-demography-examples-admixture
demography_model1 = species.get_demographic_model("AmericanAdmixture_4B11").model

# Demographic model for 4 population out of Africa
# https://popsim-consortium.github.io/stdpopsim-docs/stable/catalog.html#sec_catalog_homsap_models_outofafrica_4j171
# https://doi.org/10.1534/genetics.117.200493
# demography_model2 = species.get_demographic_model("OutOfAfrica_4J17").model

# Demographic model for African-Americans from Boyko et al 2008
# https://journals.plos.org/plosgenetics/article?id=10.1371/journal.pgen.1000083
# https://popsim-consortium.github.io/stdpopsim-docs/stable/catalog.html#sec_catalog_homsap_models_africa_1b08
# popultions: African_Americans
# demography_model3 = species.get_demographic_model("Africa_1B08").model

2025-03-07 10:38:05,523 - INFO - Set cache_dir to /home/lakishadavid/.cache/stdpopsim


/home/lakishadavid/computational_genetic_genealogy/.venv/lib/python3.12/site-packages/stdpopsim/catalog/HomSap/demographic_models.py:158: FutureWarning: Calling int on a single element Series is deprecated and will raise a TypeError in the future. Use int(ser.iloc[0]) instead
  time=int(extended_GF.time.head(1) - 1), rate=0
/home/lakishadavid/computational_genetic_genealogy/.venv/lib/python3.12/site-packages/stdpopsim/catalog/HomSap/demographic_models.py:161: FutureWarning: Calling int on a single element Series is deprecated and will raise a TypeError in the future. Use int(ser.iloc[0]) instead
  time=int(extended_GF.time.tail(1) + 1), rate=0


In [10]:
# Run this cell to see the demograhy model defintion

demography_model1

Demography(populations=[Population(initial_size=14474, growth_rate=0.0, name='AFR', description='Contemporary African population', extra_metadata={'id': 'AFR', 'sampling_time': 0}, default_sampling_time=0, initially_active=None, id=0), Population(initial_size=34038.718872685706, growth_rate=0.0038, name='EUR', description='Contemporary European population', extra_metadata={'id': 'EUR', 'sampling_time': 0}, default_sampling_time=0, initially_active=None, id=1), Population(initial_size=45851.568512352045, growth_rate=0.0048, name='ASIA', description='Contemporary Asian population', extra_metadata={'id': 'ASIA', 'sampling_time': 0}, default_sampling_time=0, initially_active=None, id=2), Population(initial_size=54663.56401171527, growth_rate=0.05, name='ADMIX', description='Modern admixed population', extra_metadata={'id': 'ADMIX', 'sampling_time': 0}, default_sampling_time=0, initially_active=None, id=3)], events=[MassMigration(time=12, source=3, dest=0, proportion=0.16666666666666666), MassMigration(time=12, source=3, dest=1, proportion=0.4), MassMigration(time=12, source=3, dest=2, proportion=1.0), MigrationRateChange(time=920, rate=0.0, source=-1, dest=-1), MassMigration(time=920, source=2, dest=1, proportion=1.0), PopulationParametersChange(time=920, initial_size=1861, growth_rate=0.0, population=1), MigrationRateChange(time=920, rate=0.00015, source=0, dest=1), MigrationRateChange(time=920, rate=0.00015, source=1, dest=0), MigrationRateChange(time=2040, rate=0.0, source=-1, dest=-1), MassMigration(time=2040, source=1, dest=0, proportion=1.0), PopulationParametersChange(time=5920, initial_size=7310, growth_rate=None, population=0)], migration_matrix=array([[0.00e+00, 2.50e-05, 7.80e-06, 0.00e+00],
       [2.50e-05, 0.00e+00, 3.11e-05, 0.00e+00],
       [7.80e-06, 3.11e-05, 0.00e+00, 0.00e+00],
       [0.00e+00, 0.00e+00, 0.00e+00, 0.00e+00]]))

msprime does not provide chromosome-aware simulations. However, as explained in [Simulations without a fixed pedigree](https://tskit.dev/msprime/docs/latest/ancestry.html#simulations-without-a-fixed-pedigree): <blockquote>[Nelson et al. 2020](https://doi.org/10.1371/journal.pgen.1008619) describes a few cases where simulating multiple chromosomes using the DTWF is important for accurately modeling shared patterns of variation between samples. In large simulated cohorts, where many samples can be close relatives, we need the DTWF model and multiple chromosomes to obtain the correct distribution of the number and total length of shared IBD segments. We similarly require multiple chromosomes and the DTWF model to get the correct ancestry patterns for very recently admixed populations.</blockquote>

Because we are simulating both close relatives (and sometimes samples with ancestors from multiple populations), we need chromosome-aware simulations. The following rate map takes that into account.

In [11]:
import stdpopsim
import msprime
import numpy as np
import math

species = stdpopsim.get_species("HomSap")
genetic_map = species.get_genetic_map("HapMapII_GRCh38")
# genetic_map = species.get_genetic_map("PyrhoYRI_GRCh38")

which_chromosome = list(range(1, 23))
# which_chromosome = [21, 22]

# set the recombination rate in the base pair segments separating chromosomes to log(2)
# see https://tskit.dev/msprime/docs/latest/ancestry.html#example-2-simulating-without-a-pedigree
"""
The effectively reduces the recombination probability
across the gap created by the break. However, it's
important to note that this approach is an approximation
and may not completely prevent recombination across the gap.
"""
r_break = math.log(2)

map_positions = []
map_rates = []
chrom_positions = [0]
# https://www.ncbi.nlm.nih.gov/grc/human/data
genetic_map_positions = {} # as a check for the chromosome positions when converting to multiple chromosomes
conversion_dict = {} # used to convert the chromosome positions to the original positions in the VCF file
assembly_len = 0

for chromosome in which_chromosome:

    # get_chromosome_map
    rate_map = genetic_map.get_chromosome_map(f"chr{chromosome}")
    # genetic_map_positions is a check for the chromosome positions when converting to multiple chromosomes in vcf
    genetic_map_positions[chromosome] = int(rate_map.sequence_length)
    assembly_len += rate_map.sequence_length
    # FIX (potentially): If the rate_map contains a position for a gap (e.g., centromere),
    # replace the given rate with r_break. Potentially, because wouldn't the rate there already
    # reflect a rate aligning with a high recombination rate?

    if chromosome != which_chromosome[0]:
        # print(ending_chromosome)

        # map_positions
        # To make the simulation chromosome-aware, need to create one "long chromosome" of the total needed length

        # Add the positions to map_positions
        # Because the first position of a map is 0, need the + 1 to avoid duplicate positions where maps join
        # print(rate_map.position)
        positions = [x + last_position + 1 for x in rate_map.position]
        # print(positions[0], positions[-1])
        map_positions.extend(positions)

        conversion_dict[(int(last_position + 1), int(last_position + 1 + int(rate_map.sequence_length)))] = chromosome

        # last_position helps to build the sequential "long chromosome" of the total needed length of multiple chromosomes
        # Get the last position in map_positions, which will be the last position in the previous map
        last_position = map_positions[-1]
        chrom_positions.append(int(last_position))

        # Add the map_rates
        # Because each map starts with a span rate of nan, need to add the mean rate to the first span
        # before adding the set of rates for this chromosome to map_rates
        # another option would be to assign it r_break and allow shorter segments from the edges
        shape = rate_map.rate.shape
        rates = rate_map.rate.tolist()
        rates[0] = rate_map.mean_rate
        rates = np.array(rates)
        rates.reshape(shape)
        map_rates.extend(rates)

    else:
        # Add the positions to map_positions
        map_positions.extend(rate_map.position)

        # print(rate_map.position)

        # last_position helps to build the sequential "long chromosome" of the total needed length of multiple chromosomes
        last_position = map_positions[-1]
        chrom_positions.append(int(last_position))

        # Add the map_rates
        map_rates.extend(rate_map.rate)
        conversion_dict[(int(0), int(last_position))] = chromosome


    if chromosome != which_chromosome[-1]:
        map_rates.append(r_break)

rate_map = msprime.RateMap(position=map_positions, rate=map_rates)
assembly_len_maps = int(rate_map.sequence_length)

print(f"The assembly length is {assembly_len_maps:,} bp.")
print(genetic_map_positions)
print(conversion_dict)

2025-03-07 10:38:14,048 - INFO - Downloading https://stdpopsim.s3.us-west-2.amazonaws.com/genetic_maps/HomSap/HapMapII_GRCh38.tar.gz
2025-03-07 10:38:22,859 - INFO - Saving to /home/lakishadavid/.cache/stdpopsim/genetic_maps/HomSap/HapMapII_GRCh38
The assembly length is 2,875,001,543 bp.
{1: 248956422, 2: 242193529, 3: 198295559, 4: 190214555, 5: 181538259, 6: 170805979, 7: 159345973, 8: 145138636, 9: 138394717, 10: 133797422, 11: 135086622, 12: 133275309, 13: 114364328, 14: 107043718, 15: 101991189, 16: 90338345, 17: 83257441, 18: 80373285, 19: 58617616, 20: 64444167, 21: 46709983, 22: 50818468}
{(0, 248956422): 1, (248956423, 491149952): 2, (491149953, 689445512): 3, (689445513, 879660068): 4, (879660069, 1061198328): 5, (1061198329, 1232004308): 6, (1232004309, 1391350282): 7, (1391350283, 1536488919): 8, (1536488920, 1674883637): 9, (1674883638, 1808681060): 10, (1808681061, 1943767683): 11, (1943767684, 2077042993): 12, (2077042994, 2191407322): 13, (2191407323, 2298451041): 14, (

With some additional work, you could modify this code to use sex specific genetic maps and/or simulate individuals by sex for the sex chromosomes.

In [12]:
import pytz  # Ensure pytz is imported

CST = pytz.timezone("US/Central")
Ghana_Time = pytz.timezone("Africa/Accra")

print(CST)


US/Central


### msprime pedigree builder

In [13]:
ped_sim_fam = pd.read_csv(os.path.join(results_directory, "pedigree.fam"), header=None, sep="\t")
ped_sim_fam.columns = ["famid", "ind", "parent0", "parent1", "sex", "phenotype"]

# Convert the 'ind' column to integer type
ped_sim_fam['ind'] = ped_sim_fam['ind'].astype(int)

# Replace 0 values with -1 in the "parent0" and "parent1" columns
ped_sim_fam["parent0"] = ped_sim_fam["parent0"].replace(0, -1)
ped_sim_fam["parent1"] = ped_sim_fam["parent1"].replace(0, -1)
ped_sim_fam.head()

famid  ind  parent0  parent1  sex  phenotype
0   FAM    1       -1       -1    1         -9
1   FAM    2       -1       -1    2         -9
2   FAM    3        1        2    1         -9
3   FAM    4       -1       -1    2         -9
4   FAM    5        1        2    1         -9

In [14]:
import numpy as np

def assign_generations(ped_df):
    # Initialize generations
    ped_df['generation'] = np.where((ped_df['parent0'] == -1) & (ped_df['parent1'] == -1), 0, -1)
    # print(ped_df['generation'])
    
    # Function to get generation
    def get_generation(ind):
        row = ped_df.loc[ped_df['ind'] == ind]
        if row['generation'].values[0] != -1:
            return row['generation'].values[0]
        parent0_gen = get_generation(row['parent0'].values[0]) if row['parent0'].values[0] != -1 else 0
        parent1_gen = get_generation(row['parent1'].values[0]) if row['parent1'].values[0] != -1 else 0
        gen = max(parent0_gen, parent1_gen) + 1
        ped_df.loc[ped_df['ind'] == ind, 'generation'] = gen
        return gen
    
    # Assign generations
    for ind in ped_df['ind']:
        gen = get_generation(ind)
        # print(gen)
    
    # Update spouse generations
    for _, row in ped_df.iterrows():
        if row['parent0'] == -1 and row['parent1'] == -1:
            children = ped_df[(ped_df['parent0'] == row['ind']) | (ped_df['parent1'] == row['ind'])]
            if not children.empty:
                child_gen = children['generation'].min()
                ped_df.loc[ped_df['ind'] == row['ind'], 'generation'] = child_gen - 1
    
    # Reverse generations
    max_gen = ped_df['generation'].max()
    ped_df['generation'] = max_gen - ped_df['generation']
    
    return ped_df


# Apply the function
ped_sim_fam = assign_generations(ped_sim_fam)

# Display the result
ped_sim_fam.head(20)

famid  ind  parent0  parent1  sex  phenotype  generation
0    FAM    1       -1       -1    1         -9           5
1    FAM    2       -1       -1    2         -9           5
2    FAM    3        1        2    1         -9           4
3    FAM    4       -1       -1    2         -9           4
4    FAM    5        1        2    1         -9           4
5    FAM    6       -1       -1    2         -9           4
6    FAM    7        3        4    1         -9           3
7    FAM    8       -1       -1    2         -9           3
8    FAM    9        5        6    1         -9           3
9    FAM   10       -1       -1    2         -9           3
10   FAM   11        7        8    1         -9           2
11   FAM   12       -1       -1    2         -9           2
12   FAM   13        9       10    1         -9           2
13   FAM   14       -1       -1    2         -9           2
14   FAM   15       11       12    1         -9           1
15   FAM   16       -1       -1    2         -9           1
16   FAM   17       13       14    1         -9           1
17   FAM   18       -1       -1    2         -9           1
18   FAM   19       15       16    1         -9           0
19   FAM   20       17       18    1         -9           0

In [15]:
# This function converts the text pedigree we created to a msprime pedigree
import tskit 

text_pedigree = ped_sim_fam.copy()

def add_individuals_to_pedigree(pb, text_pedigree):
    """
    msprime pedigree builder.
    Loops through each individual in text pedigree and adds the individual to msprime pedigree with:
    parents, time, population, and metadata of individual_name from text pedigree.
    """
    # Dictionary linking text_pedigree ids to msprime ids
    txt_ped_to_tskit_key = {}

    # For each individual in the genealogy
    for i in text_pedigree.index:
        ind_id = text_pedigree["ind"][i]
        parent0_id = text_pedigree["parent0"][i]
        parent1_id = text_pedigree["parent1"][i]
        ind_time = text_pedigree["generation"][i]
        pop = "AFR"

        # Tells msprime to simulate only generation 0 in the sample
        include_sample = ind_time == 0

        # ped-sim either gives both parents or no parents
        if parent0_id == -1 and parent1_id == -1:
            parent = pb.add_individual(
                time=ind_time,
                population=pop,
                is_sample=include_sample,
                metadata={
                    "individual_name": str(ind_id),
                    "parent0_name": int(parent0_id),
                    "parent1_name": int(parent1_id),
                    "generation": int(ind_time),
                    "population": str(pop)
                }
            )
            txt_ped_to_tskit_key[ind_id] = parent
        else:
            parent0 = txt_ped_to_tskit_key[parent0_id] if parent0_id != -1 else tskit.NULL
            parent1 = txt_ped_to_tskit_key[parent1_id] if parent1_id != -1 else tskit.NULL
            child = pb.add_individual(
                time=ind_time,
                population=pop,
                parents=[parent0, parent1],
                is_sample=include_sample,
                metadata={
                    "individual_name": str(ind_id),
                    "parent0_name": int(parent0_id),
                    "parent1_name": int(parent1_id),
                    "generation": int(ind_time),
                    "population": str(pop)
                }
            )
            txt_ped_to_tskit_key[ind_id] = child

    return pb, txt_ped_to_tskit_key

# Set so that the follow-up recapitation simulations will use the defined
# demography model. Necessary when drawing founders from multiple populations
pb = msprime.PedigreeBuilder(
    demography_model1,
    individuals_metadata_schema=tskit.MetadataSchema.permissive_json()
    )

# Build out the pedigree using input text pedigree
pb, txt_ped_to_tskit_key = add_individuals_to_pedigree(pb, text_pedigree)

# Set the initial state of tree sequence
pedigree = pb.finalise(sequence_length = assembly_len_maps)

print(pedigree)

TableCollection

Sequence Length: 2875001543.0
Time units: generations
Metadata: b''

Individuals
╔══╤═════╤════════╤═══════╤════════════════════════════════════════╗
║id│flags│location│parents│metadata                                ║
╠══╪═════╪════════╪═══════╪════════════════════════════════════════╣
║0 │    0│        │ -1, -1│{'generation': 5, 'individual_name': ...║
║1 │    0│        │ -1, -1│{'generation': 5, 'individual_name': ...║
║2 │    0│        │   0, 1│{'generation': 4, 'individual_name': ...║
║3 │    0│        │ -1, -1│{'generation': 4, 'individual_name': ...║
║4 │    0│        │   0, 1│{'generation': 4, 'individual_name': ...║
║5 │    0│        │ -1, -1│{'generation': 4, 'individual_name': ...║
║6 │    0│        │   2, 3│{'generation': 3, 'individual_name': ...║
║7 │    0│        │ -1, -1│{'generation': 3, 'individual_name': ...║
║8 │    0│        │   4, 5│{'generation': 3, 'individual_name': ...║
║9 │    0│        │ -1, -1│{'generation': 3, 'individual_name': ...║
║10│ 

### Plot the pedigree

Now we plot the pedigree as a sanity check to make sure that it looks like the pedigree we intended. Check your results directory to see more details in the diagram.

In [16]:
def draw_pedigree(pedigree):
    fig = plt.figure(num=None, figsize=(250, 100), dpi=100)
    G = nx.DiGraph()

    for ind_id, table_row in enumerate(pedigree.individuals):
        # get info from the first node of two nodes for each individual
        node_info = pedigree.nodes[pedigree.nodes.individual == ind_id]
        time = int(node_info.time[0])
        pop = node_info.population[0]

        # add the individual as the graph node
        G.add_node(ind_id, time=time, population=pop)
        for p in table_row.parents:
            if p != tskit.NULL:
                G.add_edge(ind_id, p)

    pos = nx.multipartite_layout(G, subset_key="time", align="horizontal")
    colors = plt.rcParams['axes.prop_cycle'].by_key()['color']
    node_colors = [colors[node_attr["population"]] for node_attr in G.nodes.values()]

    nx.draw_networkx(G, pos, node_size=3000, with_labels=True, node_color=node_colors,
            bbox=dict(facecolor="none", edgecolor='black', boxstyle='round, pad=0.2'))

    filename = f"diagram_msprime_pedigree.svg"
    plt.title("msprime Pedigree")
    plt.savefig(os.path.join(results_directory, filename), bbox_inches = 'tight', pad_inches = 0)

    return G

G = draw_pedigree(pedigree)

### Simulate the tree sequences

In [ ]:
from datetime import datetime
from time import process_time

# This tells the sim_ancestry function to generate a certain number of separate, independent simulation replicates.
num_replicates = 10

t1_start = process_time()

now_est = datetime.now(CST)
print("Checkpoint 1: Simulation with the Fixed Pedigree - ", now_est.strftime("%B %d, %-I:%M:%S %p %Z"))

ped_ts_replicates = msprime.sim_ancestry(
    initial_state = pedigree,
    recombination_rate = rate_map,
    model = "fixed_pedigree",
    record_provenance=False,
    discrete_genome = True,
    num_replicates = num_replicates
    )


for replicate_index, ts in enumerate(ped_ts_replicates):

    now_est = datetime.now(CST)
    print(f"Checkpoint 2: for ts in ancestry_reps step - {replicate_index}", now_est.strftime("%B %d, %-I:%M:%S %p %Z"))

    completed_ts = msprime.sim_ancestry(
        initial_state = ts,
        recombination_rate = rate_map,
        demography = demography_model1,
        model=[
            msprime.DiscreteTimeWrightFisher(duration=25),
            msprime.StandardCoalescent(),
        ],
        record_provenance=False
        )   
    mutated_ts = msprime.sim_mutations(
        completed_ts, 
        rate=mutation_rate)
    
    # Save the tree sequence
    ts_filename = f"{results_directory}/msprime_tree_replicate_{replicate_index}.trees"
    mutated_ts.dump(ts_filename)

    now_est = datetime.now(Ghana_Time)
    print(f"Checkpoint 3: for ts in ancestry_reps step - {replicate_index}", now_est.strftime("%B %d, %-I:%M:%S %p %Z"))


# remove centromere
# ts = ts.delete_intervals(intervals = centromere_intervals)
# modify sequence length to include `right` telomere

# # Remove centromeres from the simulated tree sequence
# ts = ts.delete_intervals(intervals=centromere_intervals)

# # Modify sequence length to include the right telomere
# telomere_length = 10000  # Adjust the telomere length as needed
# ts = ts.rtrim()
# ts = ts.ltrim(telomere_length)

t1_stop = process_time()

runtime = t1_stop - t1_start
hours = runtime // 3600
minutes = (runtime % 3600) // 60
seconds = (runtime % 3600) % 60

print(f"Runtime: {hours:.0f}:{minutes:.0f}:{seconds:.0f}\n")

Checkpoint 1: Simulation with the Fixed Pedigree -  March 07, 8:17:01 PM CST
2025-03-07 20:17:02,099 - INFO - Starting replicate 0
2025-03-07 20:17:02,100 - INFO - model[0] {'name': 'fixed_pedigree'} started at time=0 nodes=104 edges=0
2025-03-07 20:17:02,102 - INFO - Running model {'name': 'fixed_pedigree'} until max time: inf
2025-03-07 20:17:02,109 - INFO - Completed at time=5 nodes=104 edges=2209
Checkpoint 2: for ts in ancestry_reps step - 0 March 07, 8:17:02 PM CST
2025-03-07 20:17:02,336 - INFO - Starting replicate 0
2025-03-07 20:17:02,337 - INFO - model[0] {'name': 'dtwf'} started at time=0 nodes=104 edges=2209
2025-03-07 20:17:02,338 - INFO - Running model {'name': 'dtwf'} until max time: 25.000000
2025-03-07 20:17:02,835 - INFO - model[1] {'name': 'hudson'} started at time=25 nodes=195 edges=2402
2025-03-07 20:17:02,835 - INFO - Running model {'name': 'hudson'} until max time: inf


A tree sequence is a series of trees that describe the ancestry of different genomic segments. Each tree represents the relationships between individuals for a specific segment of the genome.

# Tree Sequence Analysis Pipeline

This code analyzes tree sequences from msprime simulations to extract genealogical relationships and identity-by-descent (IBD) segments. Here's a breakdown of what each component does:

## Core Functions

### `analyze_tree_sequences()`
- **Purpose**: Process multiple tree sequences to extract relationship data
- **Process**:
  1. For each tree sequence, identify IBD segments between sample pairs
  2. Calculate summary statistics for each pair (total shared length, segment count)
  3. Determine genetic relationships and kinship coefficients
  4. Generate three data tables: pair summaries, segment details, and relationship classifications

### `determine_relationship()`
- **Purpose**: Classify the genetic relationship between two nodes
- **Method**: Traces paths from each node to their most recent common ancestor (MRCA)
- **Classifications**:
  - **siblings**: Both nodes one step from MRCA
  - **parent-child**: One node is the parent of the other
  - **cousins**: Both nodes two steps from MRCA
  - **distant_relatives**: For more distant relationships

### `calculate_kinship()`
- **Purpose**: Calculate the kinship coefficient between two nodes
- **Formula**: 0.5^(generational distance to MRCA), accounting for both paths
- **Examples**:
  - Identical individuals: 0.5
  - Parent-child: 0.25
  - Siblings: 0.25
  - First cousins: 0.0625

### `create_family_tree_visualization()`
- **Purpose**: Extract family tree data around a specified node
- **Data collected**:
  - Direct ancestors
  - Siblings (nodes sharing a parent)
  - Direct descendants

### `prepare_for_tsinfer()`
- **Purpose**: Format data for potential use with tsinfer for inference
- **Output**: Dictionary mapping samples to their IBD relationships

## Data Extraction Process

1. **IBD Segment Identification**:
   - Uses `ts.ibd_segments()` to find segments shared between samples
   - Filters by minimum segment length and maximum time threshold

2. **Relationship Analysis**:
   - Traces through the tree structure to determine genealogical relationships
   - Extracts MRCA nodes and their times
   - Calculates kinship coefficients based on genealogical distance

3. **Dataset Creation**:
   - **Pair Summaries**: Overall statistics for each sample pair
   - **Segment Details**: Information about each individual IBD segment
   - **Relationship Data**: Genealogical classifications and kinship metrics

## Machine Learning Preparation

The three output tables provide rich features for machine learning:

1. **Pair-level features**:
   - Total shared IBD length
   - Number of segments
   - TMRCA
   - Relationship classification

2. **Segment-level features**:
   - Segment positions (left/right boundaries)
   - Segment sizes
   - Segment-specific MRCAs and TMRCAs

3. **Relationship metrics**:
   - Kinship coefficients
   - Generational distances
   - Relationship types

This structured data provides ground truth labels for supervised learning models that aim to infer relationships from genetic data.

In [ ]:
import tskit
import pandas as pd
import numpy as np
from collections import defaultdict

ped_des_ts_list = f"{results_directory}/msprime_tree_replicate_{replicate_index}.trees"

def analyze_tree_sequences(ts_list, output_prefix="results", min_span=3e6, max_time=25):
    """
    Analyze multiple tree sequences and extract relationship data
    
    Parameters:
    ts_list -- List of tree sequence objects
    output_prefix -- Prefix for output files
    min_span -- Minimum IBD segment length in bp
    max_time -- Maximum time to look back for IBD segments
    """
    # Create empty lists to store our data
    pair_summaries = []
    segment_details = []
    relationship_data = []
    
    for ts_idx, ts in enumerate(ts_list):
        print(f"Analyzing tree sequence {ts_idx+1}/{len(ts_list)}")
        
        # Get IBD segments
        ibd_segments = ts.ibd_segments(
            min_span=min_span, 
            max_time=max_time, 
            store_pairs=True, 
            store_segments=True
        )
        
        # Analyze each pair of samples that shares IBD segments
        for node_pair, segment_list in ibd_segments.items():
            node1, node2 = node_pair
            
            # Calculate summary statistics for this pair
            total_ibd_length = sum(segment.span for segment in segment_list)
            num_segments = len(segment_list)
            
            # Get genetic relationship information using the first tree
            # (we could be more sophisticated and use a consensus)
            tree = ts.first()
            mrca_node = tree.mrca(node1, node2)
            
            if mrca_node != tskit.NULL:
                tmrca = tree.time(mrca_node)
                
                # Determine relationship type
                relationship_type = determine_relationship(tree, node1, node2)
                                
                # Add pair summary
                pair_summaries.append({
                    'ts_idx': ts_idx,
                    'node1': node1,
                    'node2': node2,
                    'mrca_node': mrca_node,
                    'tmrca': tmrca,
                    'relationship': relationship_type,
                    'total_shared_length_mbp': round(total_ibd_length / 1e6, 2),
                    'num_segments': num_segments
                })
                
                # Add relationship data
                relationship_data.append({
                    'ts_idx': ts_idx,
                    'node1': node1,
                    'node2': node2,
                    'relationship': relationship_type,
                    'kinship_coefficient': calculate_kinship(tree, node1, node2),
                    'generations_to_mrca': int(tmrca)
                })
                
                # Add segment details
                for segment in segment_list:
                    # Get MRCA specifically for this segment
                    seg_tree = ts.at(segment.left)
                    seg_mrca = seg_tree.mrca(node1, node2)
                    seg_tmrca = seg_tree.time(seg_mrca) if seg_mrca != tskit.NULL else None
                    
                    segment_details.append({
                        'ts_idx': ts_idx,
                        'node1': node1,
                        'node2': node2,
                        'left': segment.left,
                        'right': segment.right,
                        'span_mbp': round(segment.span / 1e6, 2),
                        'segment_mrca': seg_mrca,
                        'segment_tmrca': seg_tmrca
                    })
    
    # Convert to DataFrames
    pair_df = pd.DataFrame(pair_summaries)
    segment_df = pd.DataFrame(segment_details)
    relationship_df = pd.DataFrame(relationship_data)
    
    # Save the DataFrames
    pair_df.to_csv(f"{output_prefix}_pair_summaries.csv", index=False)
    segment_df.to_csv(f"{output_prefix}_segment_details.csv", index=False)
    relationship_df.to_csv(f"{output_prefix}_relationships.csv", index=False)
    
    return pair_df, segment_df, relationship_df

def determine_relationship(tree, node1, node2):
    """
    Determine the genetic relationship between two nodes
    """
    mrca = tree.mrca(node1, node2)
    if mrca == tskit.NULL:
        return "unrelated"
    
    # Get path lengths from each node to MRCA
    path_length1 = 0
    current = node1
    while current != mrca and current != tskit.NULL:
        path_length1 += 1
        current = tree.parent(current)
    
    path_length2 = 0
    current = node2
    while current != mrca and current != tskit.NULL:
        path_length2 += 1
        current = tree.parent(current)
    
    # Classify relationship based on path lengths
    if path_length1 == 1 and path_length2 == 1:
        return "siblings"
    elif path_length1 == 1 and path_length2 == 2:
        return "parent-grandchild"
    elif path_length1 == 2 and path_length2 == 1:
        return "parent-grandchild"
    elif path_length1 == 2 and path_length2 == 2:
        return "cousins"
    elif path_length1 == 0 or path_length2 == 0:
        return "same_individual"
    elif path_length1 == 1 or path_length2 == 1:
        return "parent-child"
    else:
        return f"distant_relatives_{path_length1}_{path_length2}"

def calculate_kinship(tree, node1, node2):
    """
    Calculate the kinship coefficient between two nodes
    """
    if node1 == node2:
        return 0.5
    
    mrca = tree.mrca(node1, node2)
    if mrca == tskit.NULL:
        return 0.0
    
    # Simplistic kinship calculation based on generation distance
    gen_to_mrca1 = 0
    current = node1
    while current != mrca and current != tskit.NULL:
        gen_to_mrca1 += 1
        current = tree.parent(current)
    
    gen_to_mrca2 = 0
    current = node2
    while current != mrca and current != tskit.NULL:
        gen_to_mrca2 += 1
        current = tree.parent(current)
    
    # Kinship coefficient calculation (simplified)
    return 0.5 ** (gen_to_mrca1 + gen_to_mrca2)

def create_family_tree_visualization(ts, focal_node, output_file=None, generations_up=2, generations_down=2):
    """
    Create a visualization of the family tree around a focal node
    
    Parameters:
    ts -- Tree sequence
    focal_node -- Node to center the visualization on
    output_file -- File to save the visualization to (if None, displays plot)
    generations_up -- Number of ancestral generations to include
    generations_down -- Number of descendant generations to include
    """
    import networkx as nx
    import matplotlib.pyplot as plt
    from matplotlib.colors import LinearSegmentedColormap
    
    # Create a directed graph
    G = nx.DiGraph()
    
    # Get the first tree (we could alternatively use a specific position)
    tree = ts.first()
    
    # Function to add ancestors recursively
    def add_ancestors(node, current_gen=0, max_gen=generations_up):
        if current_gen >= max_gen or node == tskit.NULL:
            return
            
        parent = tree.parent(node)
        if parent != tskit.NULL:
            # Add edge from parent to child (directed graph goes from parent to child)
            G.add_edge(parent, node)
            # Label the node with its time
            G.nodes[parent]['time'] = tree.time(parent)
            G.nodes[node]['time'] = tree.time(node)
            
            # Add attributes for visualization
            G.nodes[parent]['generation'] = current_gen + 1
            
            # Continue recursively
            add_ancestors(parent, current_gen + 1, max_gen)
            
            # Add siblings (other children of this parent)
            for sibling in tree.children(parent):
                if sibling != node and sibling not in G:
                    G.add_edge(parent, sibling)
                    G.nodes[sibling]['time'] = tree.time(sibling)
                    G.nodes[sibling]['generation'] = current_gen
    
    # Function to add descendants recursively
    def add_descendants(node, current_gen=0, max_gen=generations_down):
        if current_gen >= max_gen:
            return
            
        # Add all children
        for child in tree.children(node):
            G.add_edge(node, child)
            G.nodes[child]['time'] = tree.time(child)
            G.nodes[child]['generation'] = -current_gen - 1
            
            # Continue recursively
            add_descendants(child, current_gen + 1, max_gen)
    
    # Add the focal node
    G.add_node(focal_node)
    G.nodes[focal_node]['time'] = tree.time(focal_node)
    G.nodes[focal_node]['generation'] = 0
    G.nodes[focal_node]['focal'] = True
    
    # Build the family tree
    add_ancestors(focal_node)
    add_descendants(focal_node)
    
    # Create positions for the nodes - hierarchical layout
    # Group nodes by generation
    generation_groups = {}
    for node in G.nodes():
        gen = G.nodes[node]['generation']
        if gen not in generation_groups:
            generation_groups[gen] = []
        generation_groups[gen].append(node)
    
    # Create positions dictionary
    pos = {}
    generations = sorted(generation_groups.keys())
    for i, gen in enumerate(generations):
        nodes = generation_groups[gen]
        y = -gen  # Negative because generations increase going up
        
        # Distribute nodes horizontally
        for j, node in enumerate(sorted(nodes)):
            x = j - len(nodes)/2  # Center nodes horizontally
            pos[node] = (x, y)
    
    # Draw the graph
    plt.figure(figsize=(12, 8))
    
    # Create custom color map for nodes based on generation
    min_gen = min(generations)
    max_gen = max(generations)
    gen_range = max_gen - min_gen
    
    # Node colors based on generation
    node_colors = []
    for node in G.nodes():
        if 'focal' in G.nodes[node] and G.nodes[node]['focal']:
            # Focal node is a different color (red)
            node_colors.append('red')
        else:
            # Other nodes are colored by generation
            gen = G.nodes[node]['generation']
            # Normalize to [0, 1] range for colormap
            normalized_gen = (gen - min_gen) / gen_range if gen_range > 0 else 0.5
            # Use the blue to green colormap
            node_colors.append(plt.cm.viridis(normalized_gen))
    
    # Draw nodes and edges
    nx.draw_networkx_nodes(G, pos, node_size=700, node_color=node_colors)
    nx.draw_networkx_edges(G, pos, edge_color='gray', arrows=True, arrowsize=15)
    
    # Label nodes with their IDs
    labels = {node: f"{node}\nt={G.nodes[node]['time']:.1f}" for node in G.nodes()}
    nx.draw_networkx_labels(G, pos, labels=labels, font_size=8)
    
    plt.title(f"Family Tree Centered on Node {focal_node}")
    plt.axis('off')
    
    # Add a legend for generations
    handles = []
    labels = []
    cmap = plt.cm.viridis
    for gen in sorted(set(G.nodes[node]['generation'] for node in G.nodes())):
        if gen == 0:
            color = 'red'
            label = "Focal Node (Gen 0)"
        else:
            normalized_gen = (gen - min_gen) / gen_range if gen_range > 0 else 0.5
            color = cmap(normalized_gen)
            if gen > 0:
                label = f"Ancestors (Gen {gen})"
            else:
                label = f"Descendants (Gen {-gen})"
        handles.append(plt.Line2D([0], [0], marker='o', color='w', markerfacecolor=color, markersize=10))
        labels.append(label)
    
    plt.legend(handles, labels, loc='upper right')
    
    # Save or show
    if output_file:
        plt.savefig(output_file, dpi=300, bbox_inches='tight')
        print(f"Family tree saved to {output_file}")
    else:
        plt.tight_layout()
        plt.show()
    
    # Return the graph and node data for further analysis
    family_data = {
        "focal_node": focal_node,
        "ancestors": [n for n in G.nodes() if G.nodes[n]['generation'] > 0],
        "descendants": [n for n in G.nodes() if G.nodes[n]['generation'] < 0],
        "same_generation": [n for n in G.nodes() if G.nodes[n]['generation'] == 0 and n != focal_node]
    }
    
    return G, family_data

# Function to prepare data for tsinfer
def prepare_for_tsinfer(ts, segment_df):
    """
    Prepare data that could be useful for tsinfer
    
    Parameters:
    ts -- Tree sequence
    segment_df -- DataFrame with segment information
    
    Returns:
    Dictionary with sample data that could be provided to tsinfer
    """
    # This is a simplified version - a real implementation would need more work
    sample_data = {}
    
    # Get all sample nodes
    samples = ts.samples()
    
    # For each sample, record their IBD relationships
    for sample in samples:
        # Find all segments where this sample is involved
        sample_segments = segment_df[(segment_df['node1'] == sample) | (segment_df['node2'] == sample)]
        
        if len(sample_segments) > 0:
            # Record which other samples share IBD with this one and where
            ibd_relationships = []
            for _, row in sample_segments.iterrows():
                other_node = row['node2'] if row['node1'] == sample else row['node1']
                ibd_relationships.append({
                    'other_node': other_node,
                    'left': row['left'],
                    'right': row['right'],
                    'span_mbp': row['span_mbp']
                })
            
            sample_data[sample] = {
                'ibd_relationships': ibd_relationships,
                'total_ibd_segments': len(ibd_relationships)
            }
    
    return sample_data

# Usage example
if __name__ == "__main__":
    # Assuming ped_des_ts_list contains your tree sequences
    pair_df, segment_df, relationship_df = analyze_tree_sequences(ped_des_ts_list, output_prefix="genetic_data")
    
    # Print some summary information
    print(f"Found {len(pair_df)} IBD-sharing pairs across all simulations")
    print(f"Relationship distribution:")
    print(relationship_df['relationship'].value_counts())
    
    # For the first tree sequence, prepare data for tsinfer
    tsinfer_data = prepare_for_tsinfer(ped_des_ts_list[0], 
                                       segment_df[segment_df['ts_idx'] == 0])
    
    # Create and display a family tree for a specific node
    if len(ped_des_ts_list) > 0:
        first_sample = ped_des_ts_list[0].samples()[0]
        G, family_data = create_family_tree_visualization(
            ped_des_ts_list[0], 
            first_sample,
            output_file="family_tree.png"
        )
        
        print(f"Family tree created for node {first_sample}")
        print(f"  {len(family_data['ancestors'])} ancestors visualized")
        print(f"  {len(family_data['descendants'])} descendants visualized")
        print(f"  {len(family_data['same_generation'])} nodes in same generation")